In [32]:
import pandas as pd
import numpy as np
from geopy.distance import geodesic

### accessibility score: 
- distance to airport 
- distance to train stations
- altitude?

In [33]:
df_municipalities = pd.read_csv("../data/processed/filtered_municipalities.csv")
df_airports = pd.read_csv("../data/processed/filtered_airports.csv")
df_railway = pd.read_csv("../data/processed/filtered_trains.csv")

In [34]:
df_municipalities.head()

province municipality_name  population  male  female  \
0    Álava  Alegría-Dulantzi        2971  1531    1440   
1    Álava           Amurrio       10330  5149    5181   
2    Álava           Aramaio        1381   709     672   
3    Álava        Artziniega        1856   913     943   
4    Álava           Armiñón         247   127     120   

  municipality_name_clean province_clean  altitude  longitude  latitude  cmun  
0        alegria-dulantzi          alava  561.6857  -2.513507  42.84149  1001  
1                 amurrio          alava  219.6910  -3.001022  43.05265  1002  
2                 aramaio          alava  381.8797  -2.566000  43.05400  1003  
3              artziniega          alava  196.9808  -3.128209  43.12220  1004  
4                 arminon          alava  463.5815  -2.872574  42.72305  1006

In [35]:
df_airports.head()

airport_id                         airport_name   latitude  longitude
0           1                  Aeropuerto de Jerez  36.743828  -6.062658
1           2                   Aeropuerto de Vigo  42.225740  -8.630491
2           3                Aeropuerto de Badajoz  38.889845  -6.821121
3           4  Aeropuerto de Granada - Jaén F.G.L.  37.186826  -3.778613
4           5                Aeropuerto de Almería  36.844781  -2.371234

In [36]:
df_railway.sample(15)

station_code            station_name   latitude  longitude  \
453         71210                    Flix  41.229399   0.540074   
58          40002               Calamonte  38.887492  -6.382688   
268         78501  Sant Guim De Freixenet  41.655907   1.420593   
390         23009                 Catoira  42.672220  -8.725385   
37          37606                 Badajoz  38.890610  -6.981756   
417         12010              El Espinar  40.740831  -4.189516   
557         70502        Alhama De Aragon  41.294355  -1.904278   
124         20317                  Curtis  43.127213  -8.143204   
212         78302                 Binefar  41.849766   0.291372   
32          10300      Herradon-La Cañada  40.599334  -4.495032   
305         55001               Campillos  37.032190  -4.863510   
317         61307               Cartagena  37.605022  -0.975000   
136         21002                    Miño  43.342330  -8.205388   
516         60207              El Romeral  39.694014  -3.430023   
213         74211              Sabiñanigo  42.520417  -0.373314   

    province_clean municipality_name_clean  
453      tarragona                    flix  
58         badajoz               calamonte  
268         lleida  sant guim de freixenet  
390     pontevedra                 catoira  
37         badajoz                 badajoz  
417        segovia             espinar, el  
557       zaragoza        alhama de aragon  
124      coruna, a                  curtis  
212         huesca                 binefar  
32           avila     herradon de pinares  
305         malaga               campillos  
317         murcia               cartagena  
136      coruna, a                    mino  
516         toledo             romeral, el  
213         huesca              sabinanigo

In [37]:
def find_nearest_airport(row):
    print(row)
    municipality_location = (row['latitude'], row['longitude'])
    # Calculate distance from the town to every airport
    distances = df_airports.apply(lambda x: geodesic(municipality_location, (x['latitude'], x['longitude'])).kilometers, axis=1)
    # Find the index of the airport with the smallest distance
    nearest_index = distances.idxmin()
    # Retrieve the minimum distance and corresponding airport ID
    nearest_distance = distances[nearest_index]
    nearest_airport = df_airports.loc[nearest_index, 'airport_name']
    return pd.Series([nearest_distance, nearest_airport])



In [38]:
# Apply the function to each row in the towns DataFrame and create two new columns
df_municipalities[['closest_distance', 'nearest_airport']] = df_municipalities.apply(find_nearest_airport, axis=1)


province                              Álava
municipality_name          Alegría-Dulantzi
population                             2971
male                                   1531
female                                 1440
municipality_name_clean    alegria-dulantzi
province_clean                        alava
altitude                           561.6857
longitude                         -2.513507
latitude                           42.84149
cmun                                   1001
Name: 0, dtype: object
province                      Álava
municipality_name           Amurrio
population                    10330
male                           5149
female                         5181
municipality_name_clean     amurrio
province_clean                alava
altitude                    219.691
longitude                 -3.001022
latitude                   43.05265
cmun                           1002
Name: 1, dtype: object
province                      Álava
municipality_name           Aramaio
po

In [39]:
df_municipalities.head()

province municipality_name  population  male  female  \
0    Álava  Alegría-Dulantzi        2971  1531    1440   
1    Álava           Amurrio       10330  5149    5181   
2    Álava           Aramaio        1381   709     672   
3    Álava        Artziniega        1856   913     943   
4    Álava           Armiñón         247   127     120   

  municipality_name_clean province_clean  altitude  longitude  latitude  cmun  \
0        alegria-dulantzi          alava  561.6857  -2.513507  42.84149  1001   
1                 amurrio          alava  219.6910  -3.001022  43.05265  1002   
2                 aramaio          alava  381.8797  -2.566000  43.05400  1003   
3              artziniega          alava  196.9808  -3.128209  43.12220  1004   
4                 arminon          alava  463.5815  -2.872574  42.72305  1006   

   closest_distance        nearest_airport  
0         18.273217  Aeropuerto de Vitoria  
1         28.762394   Aeropuerto de Bilbao  
2         23.639652  Aeropuerto de Vitoria  
3         26.840606   Aeropuerto de Bilbao  
4         20.846277  Aeropuerto de Vitoria

In [40]:
def find_nearest_location(row, df_location, location_name):
    municipality_location = (row['latitude'], row['longitude'])
    # Calculate distance from the town to every airport
    distances = df_location.apply(lambda x: geodesic(municipality_location, (x['latitude'], x['longitude'])).kilometers, axis=1)
    # Find the index of the airport with the smallest distance
    nearest_index = distances.idxmin()
    # Retrieve the minimum distance and corresponding airport ID
    nearest_distance = distances[nearest_index]
    nearest_location = df_location.loc[nearest_index, location_name]
    return pd.Series([nearest_distance, nearest_location])


# Apply the function to each row in the towns DataFrame and create two new columns
df_municipalities[['closest_distance_train', 'nearest_train_station']] = df_municipalities.apply(lambda row: find_nearest_location(row, df_railway, 'station_name'), axis=1)


In [41]:
df_municipalities

province      municipality_name  population   male  female  \
0        Álava       Alegría-Dulantzi        2971   1531    1440   
1        Álava                Amurrio       10330   5149    5181   
2        Álava                Aramaio        1381    709     672   
3        Álava             Artziniega        1856    913     943   
4        Álava                Armiñón         247    127     120   
...        ...                    ...         ...    ...     ...   
7947  Zaragoza                   Biel         170    104      66   
7948  Zaragoza               Marracos          85     43      42   
7949  Zaragoza  Villamayor de Gállego        2854   1446    1408   
7950     Ceuta                  Ceuta       83229  41980   41249   
7951   Melilla                Melilla       85811  43154   42657   

     municipality_name_clean province_clean   altitude  longitude  latitude  \
0           alegria-dulantzi          alava  561.68570  -2.513507  42.84149   
1                    amurrio          alava  219.69100  -3.001022  43.05265   
2                    aramaio          alava  381.87970  -2.566000  43.05400   
3                 artziniega          alava  196.98080  -3.128209  43.12220   
4                    arminon          alava  463.58150  -2.872574  42.72305   
...                      ...            ...        ...        ...       ...   
7947                    biel       zaragoza  754.24450  -0.936588  42.38749   
7948                marracos       zaragoza  404.73610  -0.776047  42.09059   
7949   villamayor de gallego       zaragoza  231.12340  -0.773315  41.68518   
7950                   ceuta          ceuta   13.47725  -5.316195  35.88829   
7951                 melilla        melilla   10.33370  -2.938794  35.29234   

       cmun  closest_distance                nearest_airport  \
0      1001         18.273217          Aeropuerto de Vitoria   
1      1002         28.762394           Aeropuerto de Bilbao   
2      1003         23.639652          Aeropuerto de Vitoria   
3      1004         26.840606           Aeropuerto de Bilbao   
4      1006         20.846277          Aeropuerto de Vitoria   
...     ...               ...                            ...   
7947  50901         61.667966  Aeropuerto de Huesca Pirineos   
7948  50902         37.961861  Aeropuerto de Huesca Pirineos   
7949  50903         23.955690         Aeropuerto de Zaragoza   
7950  51001          1.008709            Helipuerto de Ceuta   
7951  52001          2.132231          Aeropuerto de Melilla   

      closest_distance_train  nearest_train_station  
0                   0.819736       Alegria-Dulantzi  
1                  30.756835     Nanclares-Langraiz  
2                  23.176277       Alegria-Dulantzi  
3                  43.021998     Nanclares-Langraiz  
4                   2.240750               Manzanos  
...                      ...                    ...  
7947               17.531651                 Riglos  
7948               12.495085       Valença Do Minho  
7949                9.820085  Villanueva De Gallego  
7950               29.010931              Algeciras  
7951              176.572577                Almeria  

[7952 rows x 15 columns]

In [42]:
df_municipalities.to_csv("../data/scored/accessibility.csv", index=False)